In [1]:
# pip install Pillow

In [2]:
# import pymongo
# from pymongo import MongoClient
# from gridfs import *
# import os
# import glob
# # 與 MongoDB連線
# client = pymongo.MongoClient(host="mongodb", port=27017)
# #取得對應的collection
# db=client.image

# #列出目錄下的所有圖片
# files = os.listdir("/home/jovyan/work/Souvenir_pic")
# # print(files[1:])
# for i,p in enumerate(files[1:]):
#     files_1 = glob.glob("/home/jovyan/work/Souvenir_pic/" + p + "/*.jpg")
# #     print(files_1)
#     #遍歷圖片目錄集合
#     for file in files_1:
# #         print(type(file))
#         #圖片的全路徑
# #         print(file.split('/')[-1])
#         f = file.split('/')[-1]
#         file_name = f.split('.')
# #         print(file_name)      
#         #讀取建立檔案
#         datatmp = open(file, 'rb')
# #         print(datatmp)
#         #建立寫入流
#         imgput = GridFS(db)
#         print(type(imgput))
#         #將資料寫入，檔案型別和名稱通過前面的分割得到
#         insertimg=imgput.put(datatmp,content_type=f[1],file_name=f[0])
#         print(type(insertimg))
#         datatmp.close() #關閉檔案
# client.close()

In [3]:
# import pymongo
# from pymongo import MongoClient
# from gridfs import *
# import bson.binary
# import os
# import glob

# client = pymongo.MongoClient(host="mongodb", port=27017)
# db = client.image
# myset = db.img

# #列出目錄下的所有圖片
# files = os.listdir("/home/jovyan/work/Souvenir_pic")
# # print(files[1:])
# for i,p in enumerate(files[1:]):
#     files_1 = glob.glob("/home/jovyan/work/Souvenir_pic/" + p + "/*.jpg")
# #     print(files_1)
#     #遍歷圖片目錄集合
#     for file in files_1:
# #         print(file)
#         #圖片的全路徑
#         filename=file.split('/')[-1]
# #         print(filename)
    
#     f = open(file, 'rb')
# #     print(f)
# #     print(type(f))
    
#     #轉換為mongodb二進位數據儲存形式
#     content = bson.binary.Binary(f.read())
#     print(type(content))
#     f.close()
#     #插入到數據庫
#     myset.insert({'filename':filename,'data':content})
# #     print(myset)
# #     print(type(myset))
    
#     #提取資料
    
#     data = myset.find_one({'filename':filename})
# #     print(data)
#     print(data['filename'])

# client.close()    

In [13]:
import pandas as pd
from PIL import Image
import os
import glob
import pymongo
from pymongo import MongoClient
import bson.binary
import bson.objectid
import bson.errors
import joblib 
import numpy as np
import pymysql
import pymysql.cursors



#與 Mysql連線
connection = pymysql.connect(host='mysql',
                             user='root',
                             password='iii',
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)

#與 MongoDB連線
client = pymongo.MongoClient(host="mongodb", port=27017)
db = client.image
myset = db.img


queryResult=[]
distribution_0={'餅乾類':3,'小蛋糕類':2,'點心類':3,'巧克力類':1,'夾心餅乾類':1}
distribution_1={'餅乾類':3,'小蛋糕類':2,'點心類':1,'巧克力類':2,'夾心餅乾類':2}
distribution_2={'餅乾類':3,'小蛋糕類':1,'點心類':2,'巧克力類':2,'夾心餅乾類':2}


clf = joblib.load('omiyage_clf.joblib')
cluster=clf.predict(np.array([55,10,16,80000,0]).reshape((1,-1)))[0]
print(cluster)
                 #omiyage variables: 年齡, 去過次數, 去幾天 , 總預算, 性別-男:0；女:1
    
if cluster == 0:
    distribution=distribution_0
elif cluster == 1:
    distribution=distribution_1
else:
    distribution=distribution_2
    
#列出目錄下的所有圖片
files = os.listdir("/home/jovyan/work/Souvenir_pic")
# print(files[1:])
for i,p in enumerate(files[1:2]):
    files_1 = glob.glob("/home/jovyan/work/Souvenir_pic/" + p + "/*.jpg")
#     print(files_1)
    for file in files_1:
#         print(file)
        #圖片的全路徑
        filename=file.split('/')[-1]
#         print(filename)
    
    f = open(file, 'rb')
#     print(f)
#     print(type(f))    
    #轉換為mongodb二進位數據儲存形式
    content = bson.binary.Binary(f.read())
#     print(type(content))
    f.close()
    #插入到mongodb資料庫
    myset.insert({'filename':filename,'data':content})
    

#從Mysql提取關聯性資料    
with connection.cursor() as cursor:
    sql = "USE`test`"
    cursor.execute(sql)
    for kind in list(distribution.keys()): 
        cursor.execute( "SELECT * FROM `trip4.csv` WHERE Types= '"+kind+"' ORDER BY RAND() LIMIT "+str(distribution[kind]))          
        queryResult+=cursor.fetchall()
# print(len(queryResult))
# print(queryResult)
# print("========================================================")
Data = []
for i in queryResult:
    imgname = i['souvenir'] + ".jpg"
#     print(imgname)    
        #從mongodb提取圖片檔名稱
    data = myset.find_one({'filename':imgname})
    print(data)
    Data.append(data)
print(len(Data))
# print(Data)


#     for s in data({},{ "filename": 0, "data": 1, "alexa": 1 }):
#         print(s)
#     data = myset.find_one({'filename':imgname})
#     print(data['filename'])

#     print(type(data['filename'])) #class 'str'
#     print(data)
#     print(type(data)) #class 'dict'
 




#MongoDB關閉連線
client.close()

#Mysql關閉連線
connection.close()
cursor.close()

0


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:68: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.


{'_id': ObjectId('5dc00f85d8cb25cba56c17b4'), 'filename': '大江戸菓子匠\u3000銀座松崎煎餅\u3000「瓦煎餅三味胴」.jpg', 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x02\x00\x00\x01\x00\x01\x00\x00\xff\xed\x00|Photoshop 3.0\x008BIM\x04\x04\x00\x00\x00\x00\x00_\x1c\x02(\x00ZFBMD23000989030000231d0000992b00001a3d0000aa840000af9b000021bc0000e6d60000b5ed0000f8160100\x00\xff\xe2\x02\x1cICC_PROFILE\x00\x01\x01\x00\x00\x02\x0clcms\x02\x10\x00\x00mntrRGB XYZ \x07\xdc\x00\x01\x00\x19\x00\x03\x00)\x009acspAPPL\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xf6\xd6\x00\x01\x00\x00\x00\x00\xd3-lcms\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\ndesc\x00\x00\x00\xfc\x00\x00\x00^cprt\x00\x00\x01\\\x00\x00\x00\x0bwtpt\x00\x00\x01h\x00\x00\x00\x14bkpt\x00\x00\x01|\x00\x00\x00\x14rXYZ\x00\x00\x01\x90\x00\x00\x00\x14gXYZ\x00\x00

{'_id': ObjectId('5dc2634a0dd5abafae2676bb'), 'filename': 'アンド ザ フリット「ドライフリット」.jpg', 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x01\x00H\x00H\x00\x00\xff\xdb\x00C\x00\x06\x04\x05\x06\x05\x04\x06\x06\x05\x06\x07\x07\x06\x08\n\x10\n\n\t\t\n\x14\x0e\x0f\x0c\x10\x17\x14\x18\x18\x17\x14\x16\x16\x1a\x1d%\x1f\x1a\x1b#\x1c\x16\x16 , #&\')*)\x19\x1f-0-(0%()(\xff\xdb\x00C\x01\x07\x07\x07\n\x08\n\x13\n\n\x13(\x1a\x16\x1a((((((((((((((((((((((((((((((((((((((((((((((((((\xff\xc2\x00\x11\x08\x02\x80\x02\x80\x03\x01"\x00\x02\x11\x01\x03\x11\x01\xff\xc4\x00\x1c\x00\x00\x01\x05\x01\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x03\x00\x01\x02\x04\x05\x06\x07\x08\xff\xc4\x00\x19\x01\x01\x01\x01\x01\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x02\x03\x04\x05\xff\xda\x00\x0c\x03\x01\x00\x02\x10\x03\x10\x00\x00\x01\xda6\x86?\x87\x9e\xe5;7\xa3\x97\xd8\xab\xb3\xdbY\x16&\xccU\xd19\xfdz\x15\x90\x8de^\xf4x\xcc\xa8\xe9P\xe7jCL\xbc\xf3\x9e\x1b\xb4\xba\xcc\xec~\x93\x9fz!\r\x12\xeb\\\x94\xfag

{'_id': ObjectId('5dc267400dd5abafae2679ec'), 'filename': '日本茶菓SANOAH「キャラメルサンドクッキー 胡桃抹茶」.jpg', 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00\x00\x01\x00\x01\x00\x00\xff\xdb\x00C\x00\x06\x04\x05\x06\x05\x04\x06\x06\x05\x06\x07\x07\x06\x08\n\x10\n\n\t\t\n\x14\x0e\x0f\x0c\x10\x17\x14\x18\x18\x17\x14\x16\x16\x1a\x1d%\x1f\x1a\x1b#\x1c\x16\x16 , #&\')*)\x19\x1f-0-(0%()(\xff\xdb\x00C\x01\x07\x07\x07\n\x08\n\x13\n\n\x13(\x1a\x16\x1a((((((((((((((((((((((((((((((((((((((((((((((((((\xff\xc0\x00\x11\x08\x05\x00\x04\xb0\x03\x01"\x00\x02\x11\x01\x03\x11\x01\xff\xc4\x00\x1c\x00\x01\x00\x01\x05\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x02\x03\x04\x05\x06\x07\x08\xff\xc4\x00T\x10\x00\x01\x03\x02\x04\x04\x03\x04\x07\x06\x01\t\x06\x05\x01\t\x01\x00\x02\x03\x04\x11\x05\x12!1\x06AQa\x13"q\x07\x142\x81\x15BR\x91\xa1\xb1\xd1\x08\x16#3b\xc1$\x17%4rs\x92\x93\xe1\xf05CST\x82\xf1DUc\x83\xa2&6t\xb27EFdu\xc2\xff\xc4\x00\x1a\x01\x01\x01\x01\x01\x01\x01\x01\x00\x00\x00\x00\x00\x00\x00\x00\x

{'_id': ObjectId('5dc00f85d8cb25cba56c17f2'), 'filename': 'WITTAMER（ヴィタメール）「純生ショコラ」.jpg', 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00\x00\x01\x00\x01\x00\x00\xff\xe1\x00\xacExif\x00\x00MM\x00*\x00\x00\x00\x08\x00\x07\x01\x12\x00\x03\x00\x00\x00\x01\x00\x01\x00\x00\x01\x10\x00\x02\x00\x00\x00\x07\x00\x00\x00b\x01\x00\x00\x03\x00\x00\x00\x01\x00\x00\x00\x00\x87i\x00\x04\x00\x00\x00\x01\x00\x00\x00\x86\x01\x01\x00\x03\x00\x00\x00\x01\x00\x00\x00\x00\x012\x00\x02\x00\x00\x00\x14\x00\x00\x00i\x01\x0f\x00\x02\x00\x00\x00\t\x00\x00\x00}\x00\x00\x00\x00Foodie\x002018:06:08 13:19:24\x00Snowcorp\x00\x00\x02\x92\x08\x00\x04\x00\x00\x00\x01\x00\x00\x00\x00\x92\x86\x00\x02\x00\x00\x00\x04CH1\x00\x00\x00\x00\x00\xff\xdb\x00C\x00\x03\x02\x02\x03\x02\x02\x03\x03\x03\x03\x04\x03\x03\x04\x05\x08\x05\x05\x04\x04\x05\n\x07\x07\x06\x08\x0c\n\x0c\x0c\x0b\n\x0b\x0b\r\x0e\x12\x10\r\x0e\x11\x0e\x0b\x0b\x10\x16\x10\x11\x13\x14\x15\x15\x15\x0c\x0f\x17\x18\x16\x14\x18\x12\x14\x15\x14\xff\xdb\x00C\x01\x

{'_id': ObjectId('5dc26a4c0dd5abafae267cfe'), 'filename': 'ピエール・マルコリーニ 「マルコリーニ マドレーヌ ショコラ」.jpg', 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x01\x00H\x00H\x00\x00\xff\xed\x17tPhotoshop 3.0\x008BIM\x03\xed\nResolution\x00\x00\x00\x00\x10\x00H\x00\x00\x00\x01\x00\x02\x00H\x00\x00\x00\x01\x00\x028BIM\x04\r\x18FX Global Lighting Angle\x00\x00\x00\x00\x04\x00\x00\x00\x1e8BIM\x04\x19\x12FX Global Altitude\x00\x00\x00\x00\x04\x00\x00\x00\x1e8BIM\x03\xf3\x0bPrint Flags\x00\x00\x00\t\x00\x00\x00\x00\x00\x00\x00\x00\x01\x008BIM\x04\n\x0eCopyright Flag\x00\x00\x00\x00\x01\x00\x008BIM\'\x10\x14Japanese Print Flags\x00\x00\x00\x00\n\x00\x01\x00\x00\x00\x00\x00\x00\x00\x028BIM\x03\xf5\x17Color Halftone Settings\x00\x00\x00H\x00/ff\x00\x01\x00lff\x00\x06\x00\x00\x00\x00\x00\x01\x00/ff\x00\x01\x00\xa1\x99\x9a\x00\x06\x00\x00\x00\x00\x00\x01\x002\x00\x00\x00\x01\x00Z\x00\x00\x00\x06\x00\x00\x00\x00\x00\x01\x005\x00\x00\x00\x01\x00-\x00\x00\x00\x06\x00\x00\x00\x00\x00\x018BIM\x03\xf8\x17Color Tra

{'_id': ObjectId('5dc269f90dd5abafae267c81'), 'filename': 'La Famille「シフォンケーキ」.jpg', 'data': b'\xff\xd8\xff\xe1\x00\x18Exif\x00\x00II*\x00\x08\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xec\x00\x11Ducky\x00\x01\x00\x04\x00\x00\x00P\x00\x00\xff\xe1\x03/http://ns.adobe.com/xap/1.0/\x00<?xpacket begin="\xef\xbb\xbf" id="W5M0MpCehiHzreSzNTczkc9d"?> <x:xmpmeta xmlns:x="adobe:ns:meta/" x:xmptk="Adobe XMP Core 5.6-c111 79.158325, 2015/09/10-01:10:20        "> <rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#"> <rdf:Description rdf:about="" xmlns:xmp="http://ns.adobe.com/xap/1.0/" xmlns:xmpMM="http://ns.adobe.com/xap/1.0/mm/" xmlns:stRef="http://ns.adobe.com/xap/1.0/sType/ResourceRef#" xmp:CreatorTool="Adobe Photoshop CC 2015 (Windows)" xmpMM:InstanceID="xmp.iid:36160775EA4911E5AAFB9C64A7CF8910" xmpMM:DocumentID="xmp.did:36160776EA4911E5AAFB9C64A7CF8910"> <xmpMM:DerivedFrom stRef:instanceID="xmp.iid:36160773EA4911E5AAFB9C64A7CF8910" stRef:documentID="xmp.did:36160774EA4911E5

In [15]:
Data[8]

{'_id': ObjectId('5dc26a4c0dd5abafae267cfe'),
 'filename': 'ピエール・マルコリーニ 「マルコリーニ マドレーヌ ショコラ」.jpg',
 'data': b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x01\x00H\x00H\x00\x00\xff\xed\x17tPhotoshop 3.0\x008BIM\x03\xed\nResolution\x00\x00\x00\x00\x10\x00H\x00\x00\x00\x01\x00\x02\x00H\x00\x00\x00\x01\x00\x028BIM\x04\r\x18FX Global Lighting Angle\x00\x00\x00\x00\x04\x00\x00\x00\x1e8BIM\x04\x19\x12FX Global Altitude\x00\x00\x00\x00\x04\x00\x00\x00\x1e8BIM\x03\xf3\x0bPrint Flags\x00\x00\x00\t\x00\x00\x00\x00\x00\x00\x00\x00\x01\x008BIM\x04\n\x0eCopyright Flag\x00\x00\x00\x00\x01\x00\x008BIM\'\x10\x14Japanese Print Flags\x00\x00\x00\x00\n\x00\x01\x00\x00\x00\x00\x00\x00\x00\x028BIM\x03\xf5\x17Color Halftone Settings\x00\x00\x00H\x00/ff\x00\x01\x00lff\x00\x06\x00\x00\x00\x00\x00\x01\x00/ff\x00\x01\x00\xa1\x99\x9a\x00\x06\x00\x00\x00\x00\x00\x01\x002\x00\x00\x00\x01\x00Z\x00\x00\x00\x06\x00\x00\x00\x00\x00\x01\x005\x00\x00\x00\x01\x00-\x00\x00\x00\x06\x00\x00\x00\x00\x00\x018BIM\x03\xf8\x17Color T

In [ ]:
# imgname = i['souvenir'] + ".jpg"
# print(imgname)
# data = myset.find_one({'filename':imgname})
# print(data)